# <center> <span style='color:darkgreen'><u>Unruh-deWitt detector on a static BTZ black hole</u></span>

\hspace{2.5cm} <span class="plumBlack"> In this notebook, we reproduce the results of ["Comments on the anti-Hawking effect on a BTZ black hole spacetime"](https://arxiv.org/).</span>

<span style='color:royalblue'>**Libraries used:**</span> numpy, mpmath, plotly.graph_objects

<span style='color:royalblue'> **Precision matters:**</span> for dealing with arbitrary-precision floating-points, the [mp context](http://mpmath.org/doc/current/contexts.html#arbitrary-precision-floating-point-mp).

Let's consider the massless conformally-coupled scalar field on the static BTZ black hole. That is:

\begin{align}
    & \text{mass of the scalar field, } &m&=0;\nonumber\\
    & \text{conformal coupling, } &\xi R&= 0.75; \nonumber\\
    & \text{effective mass, } &\mu^2 &= -0.75; \nonumber\\
    & \text{angular momentum of the black hole, } &J&=0;\nonumber\\
    & \text{inner horizon, } &r_-&=0.\nonumber
\end{align}
    

<div class="alert alert-block alert-warning">
<b>Be careful:</b> the precision settings chosen in this notebook are good for the parameters set used here. For a different set, one will definetely need to change the values chosen for mp.dps. Notice that smaller $M$ values need higher precision settings.
</div>

# <span style='color:darkgreen'>Implementation</span>

In [54]:
import numpy as np
from mpmath import hyp2f1, mpc, mpf, gamma, mp, sin, cos, sqrt, exp, log, pi, conj
import plotly.graph_objects as go
%reload_ext jupyternotify

# the hyp2f1 from scipy.special only accepts real parameters, though complex argument.
## it is crucial to import all these functions from the mpmath because it accepts 
## arbitrary precision settings within the mp context
### from numpy just linspace, and vectorize for the plots. One could use mpmath 
### for that as well.

<IPython.core.display.Javascript object>

The black holes we are considering are determined by their mass. For that reason, we shall define a BTZ black hole class, grouping all the functions associated to each black hole, whose instances are characterized by the mass. To avoid numerical errors, the user can provide the exact root of $M$, which equals $r_+$.  

In [64]:
class BTZ:
    # class object determining BTZ black holes

    def __init__(self, M, r_plus, mu2=-0.75):
        self.M = M            # mass of the black hole
        self.r_plus = r_plus  # square root of the mass of the black hole
        self.mu2 = mu2        # effective mass for the massless conf. coup. scalar field

    def g00(self, z):
        # coefficient of dt**2 of the metric tensor
        return self.M*z/(z-1)

    def omega_tilde_00(self, omega, z):
        # blueshift effect on omega
        return mp.sqrt(abs(self.g00(z)))*omega

    def a(self, l, omega):
        return 1/2 * (1 + sqrt(1 + self.mu2) + 1j*(omega + l)/self.r_plus)
    # parameter a of the hypergeometric solutions

    def b(self, l, omega):
        return 1/2 * (1 + sqrt(1 + self.mu2) + 1j*(omega - l)/self.r_plus)
    # parameter b of the hypergeometric solutions

    def c(self, omega):
        return 1 + 1j*omega/self.r_plus
    # parameter c of the hypergeometric solutions

    def A(self, l, omega):
        return mp.gamma(self.c(omega)) * \
    mp.gamma(self.c(omega) - self.a(l, omega) - self.b(l, omega)) / \
    mp.gamma(self.c(omega) - self.a(l, omega))/mp.gamma(self.c(omega) - self.b(l, omega))
    # parameter A of the normalization constant of the transition rate

    def B(self, l, omega):
        # parameter B of the normalization constant of the transition rate
        return mp.gamma(self.c(omega))*mp.gamma(self.a(l, omega) +\
                                                    self.b(l, omega) - self.c(omega)) /\
            gamma(self.a(l, omega))/mp.gamma(self.b(l, omega))

    def factor_C(self):
        # parameter C of the normalization constant of the transition rate
        return 2/(1j*mp.pi*mp.sqrt(1 + self.mu2))

    def normalization(self, gamma, l, omega):
        return self.factor_C()*(conj(self.A(l, omega))*self.B(l, omega) -
                                self.A(l, omega) * conj(self.B(l, omega))) /\
            (abs(self.B(l, omega)*cos(gamma) - self.A(l, omega)*sin(gamma))**2)
    # normalization parameter that goes in the transition rate

    def alpha(self, omega):
        return 1j * omega / (2 * self.r_plus)
    # parameter of the ansatz of the radial solutions

    def beta_plus(self):
        # parameter of the ansatz of the radial solutions,  equals beta
        return 1/2 + mp.sqrt(1 + self.mu2)/2

    def beta_minus(self):
        # parameter of the ansatz of the radial solutions,  equals 1 - beta
        return 1/2 - mp.sqrt(1 + self.mu2)/2

    def R11(self, l, gamma, omega, z):
        # R11 and R22 form a basis of radial solutions at AdS boundary
        return z**self.alpha(omega)*(1-z)**self.beta_plus() * \
            hyp2f1(self.a(l, omega), self.b(l, omega), self.a(l, omega) +
                   self.b(l, omega) - self.c(omega) + 1, 1 - z)

    def R21(self, l, gamma, omega, z):
        # R11 and R22 form a basis of radial solutions at AdS boundary
        return z**self.alpha(omega)*(1-z)**self.beta_minus() * \
            hyp2f1(self.c(omega) - self.a(l, omega), self.c(omega) - self.b(l, omega),
                   self.c(omega) - self.a(l, omega) - self.b(l, omega) + 1, 1 - z)

    def R(self, l, gamma, omega, z):
        return mp.cos(gamma)*self.R11(l, gamma, omega, z) + mp.sin(gamma) *\
            self.R21(l, gamma, omega, z)
    # radial solution at the AdS boundary compatible with Robin b.c.

    def z_of_TH(self, TH):
        return 1/(1 + 4*pi**2*TH**2)
    # detector's position as function of the Hawking temperature

    def TH_of_z(self, z):
        return self.r_plus/(2*pi*sqrt(abs(self.g00(z))))
    # Hawking temperature as function of detector's position

    def transition_rate_0(self, gamma, l, Egap, z):
        # l-term constribution to the transition rate
        # for the ground state on the static BTZ black hole
        # as a function of the boundary contidion parametrized by gamma,
        # the quantum number l, the energy gap Egap and the position
        # of the detector z.
        x = self.normalization(gamma, l, self.omega_tilde_00(Egap, z)) * \
            self.R(l, gamma, self.omega_tilde_00(Egap, z), z)**2
        return x.real, x.imag

    def transition_rate_T(self, gamma, l, Egap, z):
        # l-term constribution to the transition rate
        # for the KMS state on the static BTZ black hole
        # as a function of the boundary contidion parametrized by gamma,
        # the quantum number l, the energy gap Egap and the position
        # of the detector z.
        x = 1/(exp(self.omega_tilde_00(Egap, z)/self.TH_of_z(z)) - 1) * \
            self.normalization(gamma, l, self.omega_tilde_00(Egap, z)) * \
            self.R(l, gamma, self.omega_tilde_00(Egap, z), z)**2
        return x.real, x.imag

The methods

``` transition_rate_static_0(gamma, l, Egap, z)```    and    ```transition_rate_static_T(gamma, l, Egap, z)``` 

give the transition rate of an Unruh-deWitt detector on the static BTZ black hole coupled to respectively, the ground state and the KMS state, of the massless conformally coupled scalar field. Let's see how they behave with respect to its parameters.

#  <span style='color:darkgreen'>M = 1</span>

\begin{align}
    & \text{mass of the black hole, } &M&=1;\nonumber\\
    & \text{outer horizon, } &r_+&=1.\nonumber
\end{align}

In [56]:
btz1 = BTZ(1, 1)

## <span style='color:brown'> The $l=0$ term of the transition rate</span>

### <span style='color:gray'>As a function of position z </span>

In [13]:
import plotly.graph_objects as go
normalization_factor = 2.75

N = 200
x = np.linspace(1e-5, 1-1e-5, N)

lp, Egapp = 0, 0.1



gamma0 = 0
def func0(p):
    return float(btz1.transition_rate_0(gamma0,lp,Egapp,p)[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

gamma1 = 0.25*np.pi
def func1(p):
    return float(btz1.transition_rate_0(gamma1,lp,Egapp,p)[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

gamma2 = 0.40*np.pi
def func2(p):
    return float(btz1.transition_rate_0(gamma2,lp,Egapp,p)[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

gamma3 = 0.47*np.pi
def func3(p):
    return float(btz1.transition_rate_0(gamma3,lp,Egapp,p)[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

gamma4 = 0.5*np.pi
def func4(p):
    return float(btz1.transition_rate_0(gamma4,lp,Egapp,p)[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y4, name='Newmann'))
fig.add_trace(go.Scatter(x=x, y=y3, name='Robin 3'))
fig.add_trace(go.Scatter(x=x, y=y2, name='Robin 2'))
fig.add_trace(go.Scatter(x=x, y=y1, name='Robin 1'))
fig.add_trace(go.Scatter(x=x, y=y0, name='Dirichlet'))


fig.update_layout(
    title="Transition rate for the Ground state as a function of position z on the static BTZ black hole",
    xaxis_title=r"$z$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Boundary Conditions"
#     ,font=dict(
#         family="Helvetica",
#         size=18,
#         color="RebeccaPurple"
#     )
)

fig.show()

In [15]:
import plotly.graph_objects as go
normalization_factor = 140

N = 200
x = np.linspace(1e-2, 1-1e-2, N)

lp, Egapp = 0, 0.1


gamma0 = 0
def func0(p):
    return float(btz1.transition_rate_T(gamma0,lp,Egapp,p)[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

gamma1 = 0.25*np.pi
def func1(p):
    return float(btz1.transition_rate_T(gamma1,lp,Egapp,p)[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

gamma2 = 0.40*np.pi
def func2(p):
    return float(btz1.transition_rate_T(gamma2,lp,Egapp,p)[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

gamma3 = 0.47*np.pi
def func3(p):
    return float(btz1.transition_rate_T(gamma3,lp,Egapp,p)[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

gamma4 = 0.5*np.pi
def func4(p):
    return float(btz1.transition_rate_T(gamma4,lp,Egapp,p)[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y4, name='Newmann'))
fig.add_trace(go.Scatter(x=x, y=y3, name='Robin 3'))
fig.add_trace(go.Scatter(x=x, y=y2, name='Robin 2'))
fig.add_trace(go.Scatter(x=x, y=y1, name='Robin 1'))
fig.add_trace(go.Scatter(x=x, y=y0, name='Dirichlet'))


fig.update_layout(
    title="Transition rate for the KMS state as a function of position z on the static BTZ black hole",
    xaxis_title=r"$z$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Boundary Conditions"
)

fig.show()

### <span style='color:gray'>As a function of the Hawking temperature </span>

In [16]:
import plotly.graph_objects as go
normalization_factor = 2.75

N = 200
x = np.linspace(1e-3, 5, N)

lp, Egapp = 0, 0.1


gamma0 = 0
def func0(T):
    return float(btz1.transition_rate_0(gamma0,lp,Egapp,btz1.z_of_TH(T))[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

gamma1 = 0.25*np.pi
def func1(T):
    return float(btz1.transition_rate_0(gamma1,lp,Egapp,btz1.z_of_TH(T))[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

gamma2 = 0.40*np.pi
def func2(T):
    return float(btz1.transition_rate_0(gamma2,lp,Egapp,btz1.z_of_TH(T))[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

gamma3 = 0.47*np.pi
def func3(T):
    return float(btz1.transition_rate_0(gamma3,lp,Egapp,btz1.z_of_TH(T))[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

gamma4 = 0.5*np.pi
def func4(T):
    return float(btz1.transition_rate_0(gamma4,lp,Egapp,btz1.z_of_TH(T))[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y4, name='Newmann'))
fig.add_trace(go.Scatter(x=x, y=y3, name='Robin 3'))
fig.add_trace(go.Scatter(x=x, y=y2, name='Robin 2'))
fig.add_trace(go.Scatter(x=x, y=y1, name='Robin 1'))
fig.add_trace(go.Scatter(x=x, y=y0, name='Dirichlet'))


fig.update_layout(
    title="Transition rate for the Ground state as a function of the Hawking temperature on the static BTZ black hole",
    xaxis_title=r"$T_H$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Boundary Conditions"
#     ,font=dict(
#         family="Helvetica",
#         size=18,
#         color="RebeccaPurple"
#     )
)

fig.show()

In [22]:
import plotly.graph_objects as go
normalization_factor = 600

N = 200
x = np.linspace(1e-2, 5, N)

lp, Egapp = 0, 0.1


gamma0 = 0
def func0(T):
    return float(btz1.transition_rate_T(gamma0,lp,Egapp,btz1.z_of_TH(T))[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

gamma1 = 0.25*np.pi
def func1(T):
    return float(btz1.transition_rate_T(gamma1,lp,Egapp,btz1.z_of_TH(T))[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

gamma2 = 0.40*np.pi
def func2(T):
    return float(btz1.transition_rate_T(gamma2,lp,Egapp,btz1.z_of_TH(T))[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

gamma3 = 0.47*np.pi
def func3(T):
    return float(btz1.transition_rate_T(gamma3,lp,Egapp,btz1.z_of_TH(T))[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

gamma4 = 0.5*np.pi
def func4(T):
    return float(btz1.transition_rate_T(gamma4,lp,Egapp,btz1.z_of_TH(T))[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y4, name='Newmann'))
fig.add_trace(go.Scatter(x=x, y=y3, name='Robin 3'))
fig.add_trace(go.Scatter(x=x, y=y2, name='Robin 2'))
fig.add_trace(go.Scatter(x=x, y=y1, name='Robin 1'))
fig.add_trace(go.Scatter(x=x, y=y0, name='Dirichlet'))


fig.update_layout(
    title="Transition rate for the KMS state as a function of the Hawking temperature on the static BTZ black hole",
    xaxis_title=r"$T_H$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Boundary Conditions"
#     ,font=dict(
#         family="Helvetica",
#         size=18,
#         color="RebeccaPurple"
#     )
)

fig.show()

### <span style='color:gray'>As a function of the energy gap </span>

In [23]:
import plotly.graph_objects as go
normalization_factor = 4.85
N = 200
x = np.linspace(1e-3, 5, N)

lp, zp = 0, 0.5


gamma0 = 0
def func0(Egap):
    return float(btz1.transition_rate_0(gamma0,lp,Egap,zp)[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

gamma1 = 0.25*np.pi
def func1(Egap):
    return float(btz1.transition_rate_0(gamma1,lp,Egap,zp)[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

gamma2 = 0.40*np.pi
def func2(Egap):
    return float(btz1.transition_rate_0(gamma2,lp,Egap,zp)[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

gamma3 = 0.47*np.pi
def func3(Egap):
    return float(btz1.transition_rate_0(gamma3,lp,Egap,zp)[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

gamma4 = 0.5*np.pi
def func4(Egap):
    return float(btz1.transition_rate_0(gamma4,lp,Egap,zp)[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y4, name='Newmann'))
fig.add_trace(go.Scatter(x=x, y=y3, name='Robin 3'))
fig.add_trace(go.Scatter(x=x, y=y2, name='Robin 2'))
fig.add_trace(go.Scatter(x=x, y=y1, name='Robin 1'))
fig.add_trace(go.Scatter(x=x, y=y0, name='Dirichlet'))


fig.update_layout(
    title="Transition rate for the Ground state as a function of the energy gap on the static BTZ black hole",
    xaxis_title=r"$E_{gap}$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Boundary Conditions"
#     ,font=dict(
#         family="Helvetica",
#         size=18,
#         color="RebeccaPurple"
#     )
)

fig.show()

In [25]:
import plotly.graph_objects as go
normalization_factor = 4.6

N = 200
x = np.linspace(1e-3, 1, N)

lp, zp = 0, 0.5


gamma0 = 0
def func0(Egap):
    return float(btz1.transition_rate_T(gamma0,lp,Egap,zp)[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

gamma1 = 0.25*np.pi
def func1(Egap):
    return float(btz1.transition_rate_T(gamma1,lp,Egap,zp)[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

gamma2 = 0.40*np.pi
def func2(Egap):
    return float(btz1.transition_rate_T(gamma2,lp,Egap,zp)[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

gamma3 = 0.47*np.pi
def func3(Egap):
    return float(btz1.transition_rate_T(gamma3,lp,Egap,zp)[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

gamma4 = 0.5*np.pi
def func4(Egap):
    return float(btz1.transition_rate_T(gamma4,lp,Egap,zp)[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y4, name='Newmann'))
fig.add_trace(go.Scatter(x=x, y=y3, name='Robin 3'))
fig.add_trace(go.Scatter(x=x, y=y2, name='Robin 2'))
fig.add_trace(go.Scatter(x=x, y=y1, name='Robin 1'))
fig.add_trace(go.Scatter(x=x, y=y0, name='Dirichlet'))


fig.update_layout(
    title="Transition rate for the KMS state as a function of the energy gap on the static BTZ black hole",
    xaxis_title=r"$E_{gap}$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Boundary Conditions"
#     ,font=dict(
#         family="Helvetica",
#         size=18,
#         color="RebeccaPurple"
#     )
)

fig.show()

## <span style='color:brown'>First few different $l$ terms</span>

### <span style='color:gray'>Dirichlet boundary condition</span>

In [26]:
normalization_factor = 2.75

N = 200
x = np.linspace(1e-3, 1-1e-3, N)

Egapp, gamma0 = 0.1, 0


l0 = 0
def func0(z):
    return float(btz1.transition_rate_0(gamma0,l0,Egapp,z)[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

l1 = 1
def func1(z):
    return float(btz1.transition_rate_0(gamma0,l1,Egapp,z)[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

l2 = 2
def func2(z):
    return float(btz1.transition_rate_0(gamma0,l2,Egapp,z)[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

l3 = 3
def func3(z):
    return float(btz1.transition_rate_0(gamma0,l3,Egapp,z)[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

l4 = 4
def func4(z):
    return float(btz1.transition_rate_0(gamma0,l4,Egapp,z)[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0, name=r'$l=0$'))
fig.add_trace(go.Scatter(x=x, y=y1, name=r'$l=1$'))
fig.add_trace(go.Scatter(x=x, y=y2, name=r'$l=2$'))
fig.add_trace(go.Scatter(x=x, y=y3, name=r'$l=3$'))
fig.add_trace(go.Scatter(x=x, y=y4, name=r'$l=4$'))


fig.update_layout(
    title="Contributions to the transition rate for the Ground state with Dirichlet b.c. on the static BTZ black hole",
    xaxis_title=r"$z$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title=""
)

fig.show()

In [27]:
normalization_factor = 2.75

N = 200
x = np.linspace(1e-3, 5, N)

Egapp, gamma0 = 0.1, 0


l0 = 0
def func0(T):
    return float(btz1.transition_rate_0(gamma0,l0,Egapp,btz1.z_of_TH(T))[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

l1 = 1
def func1(T):
    return float(btz1.transition_rate_0(gamma0,l1,Egapp,btz1.z_of_TH(T))[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

l2 = 2
def func2(T):
    return float(btz1.transition_rate_0(gamma0,l2,Egapp,btz1.z_of_TH(T))[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

l3 = 3
def func3(T):
    return float(btz1.transition_rate_0(gamma0,l3,Egapp,btz1.z_of_TH(T))[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

l4 = 4
def func4(T):
    return float(btz1.transition_rate_0(gamma0,l4,Egapp,btz1.z_of_TH(T))[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0, name=r'$l=0$'))
fig.add_trace(go.Scatter(x=x, y=y1, name=r'$l=1$'))
fig.add_trace(go.Scatter(x=x, y=y2, name=r'$l=2$'))
fig.add_trace(go.Scatter(x=x, y=y3, name=r'$l=3$'))
fig.add_trace(go.Scatter(x=x, y=y4, name=r'$l=4$'))


fig.update_layout(
    title="Contributions to the transition rate for the Ground state with Dirichlet b.c. on the static BTZ black hole",
    xaxis_title=r"$T_H$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title=""
)

fig.show()

### <span style='color:gray'>For Neumann boundary condition</span>

In [28]:
normalization_factor = 2.75

N = 200
x = np.linspace(1e-3, 1-1e-3, N)

Egapp, gamma4 = 0.1, np.pi/2


l0 = 0
def func0(z):
    return float(btz1.transition_rate_0(gamma4,l0,Egapp,z)[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

l1 = 1
def func1(z):
    return float(btz1.transition_rate_0(gamma4,l1,Egapp,z)[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

l2 = 2
def func2(z):
    return float(btz1.transition_rate_0(gamma4,l2,Egapp,z)[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

l3 = 3
def func3(z):
    return float(btz1.transition_rate_0(gamma4,l3,Egapp,z)[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

l4 = 4
def func4(z):
    return float(btz1.transition_rate_0(gamma4,l4,Egapp,z)[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0, name=r'$l=0$'))
fig.add_trace(go.Scatter(x=x, y=y1, name=r'$l=1$'))
fig.add_trace(go.Scatter(x=x, y=y2, name=r'$l=2$'))
fig.add_trace(go.Scatter(x=x, y=y3, name=r'$l=3$'))
fig.add_trace(go.Scatter(x=x, y=y4, name=r'$l=4$'))


fig.update_layout(
    title="Contributions to the transition rate for the Ground state with Neumann b.c. on the static BTZ black hole",
    xaxis_title=r"$z$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title=""
)

fig.show()

In [29]:
normalization_factor = 2.75

N = 250
x = np.linspace(1e-3,5, N)

Egapp, gamma4 = 0.1, np.pi/2


l0 = 0
def func0(T):
    return float(btz1.transition_rate_0(gamma4,l0,Egapp,btz1.z_of_TH(T))[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

l1 = 1
def func1(T):
    return float(btz1.transition_rate_0(gamma4,l1,Egapp,btz1.z_of_TH(T))[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

l2 = 2
def func2(T):
    return float(btz1.transition_rate_0(gamma4,l2,Egapp,btz1.z_of_TH(T))[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

l3 = 3
def func3(T):
    return float(btz1.transition_rate_0(gamma4,l3,Egapp,btz1.z_of_TH(T))[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

l4 = 4
def func4(T):
    return float(btz1.transition_rate_0(gamma4,l4,Egapp,btz1.z_of_TH(T))[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0, name=r'$l=0$'))
fig.add_trace(go.Scatter(x=x, y=y1, name=r'$l=1$'))
fig.add_trace(go.Scatter(x=x, y=y2, name=r'$l=2$'))
fig.add_trace(go.Scatter(x=x, y=y3, name=r'$l=3$'))
fig.add_trace(go.Scatter(x=x, y=y4, name=r'$l=4$'))


fig.update_layout(
    title="Contributions to the transition rate for the Ground state with Neumann b.c. on the static BTZ black hole",
    xaxis_title=r"$T_H$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title=""
)

fig.show()

## <span style='color:brown'>Sum in $l$</span>

### <span style='color:gray'>Precision settings exploration</span>

In [7]:
x = np.linspace(0, 15, 16)

Egapp, gamma0 = 0.1, 0


THp = 1
def func0(n):
    if n == -1:
        return 0
    return float(btz1.transition_rate_0(gamma0, n, Egapp, btz1.z_of_TH(THp))[0]) + func0(n - 1)
vfunc0 = np.vectorize(func0)
mp.dps = 15
y0Bad = (vfunc0((x)))
mp.dps = 100
y0Good = (vfunc0((x)))

THp = 10
def func1(n):
    if n == -1:
        return 0
    return float(btz1.transition_rate_0(gamma0, n, Egapp, btz1.z_of_TH(THp))[0]) + func1(n - 1)
vfunc1 = np.vectorize(func1)
mp.dps = 15
y1Bad = (vfunc1((x)))
mp.dps = 100
y1Good = (vfunc1((x)))


THp = 50
def func2(n):
    if n == -1:
        return 0
    return float(btz1.transition_rate_0(gamma0, n, Egapp, btz1.z_of_TH(THp))[0]) + func2(n - 1)
vfunc2 = np.vectorize(func2)
mp.dps = 15
y2Bad = (vfunc2((x)))
mp.dps = 100
y2Good = (vfunc2((x)))

THp = 100
def func3(n):
    if n == -1:
        return 0
    return float(btz1.transition_rate_0(gamma0, n, Egapp, btz1.z_of_TH(THp))[0]) + func3(n - 1)
vfunc3 = np.vectorize(func3)
mp.dps = 15
y3Bad = (vfunc3((x)))
mp.dps = 100
y3Good = (vfunc3((x)))


fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0Good, name='y0Good'))
fig.add_trace(go.Scatter(x=x, y=y1Good, name='y1Good'))
fig.add_trace(go.Scatter(x=x, y=y2Good, name='y2Good'))
fig.add_trace(go.Scatter(x=x, y=y3Good, name='y3Good'))
fig.add_trace(go.Scatter(x=x, y=y0Bad, name='y0Bad'))
fig.add_trace(go.Scatter(x=x, y=y1Bad, name='y1Bad'))
fig.add_trace(go.Scatter(x=x, y=y2Bad, name='y2Bad'))
fig.add_trace(go.Scatter(x=x, y=y3Bad, name='y3Bad'))

fig.update_layout(
    title={
        'xanchor': 'left',
        'yanchor': 'top'}, 
     font_color="black",
    width=800,
    height=300,
    xaxis=dict(
        showticklabels=False,
        showgrid=False,
        zeroline=False
    ),
    yaxis=dict(
        showticklabels=False,
        showgrid=False,
        zeroline=False
    ),
    showlegend=False,
    plot_bgcolor='rgb(0,0,0)'
)

fig.layout.update(
   updatemenus = [
      go.layout.Updatemenu(
         type = "buttons", direction = "right", active = 0, x = 1.4, y = 1.5,
         buttons = list(
            [
               dict(
                  label = "15", method = "update", 
                  args = [{"visible": [False,False,False,False,True,True,True, True]},{"title": "With bad precision settings, a dramatic oscillation takes place. "} ]
               ),
               dict(
                  label = "100", method = "update",
                  args = [{"visible": [True,True,True,True,False,False,False,False]},{"title": "With good precision settings, things converge beautifully. "} ]
               )
            ]
         )
      )
   ]
)
fig.update_layout(
    annotations=[
        dict(text="mp.dps", x=1.2, xref="paper", y=1.45, yref="paper",
                             align="left", showarrow=False)
    ])



fig.show()

Higher precision must be set to compute higher $l$ contributions to the transition rate. We shall work within the context [mp](http://mpmath.org/doc/current/contexts.html#arbitrary-precision-floating-point-mp) of mpmath:

In [32]:
mp.dps = 100 #default value is 15
print(mp)

Mpmath settings:
  mp.prec = 336               [default: 53]
  mp.dps = 100                [default: 15]
  mp.trap_complex = False     [default: False]


Example of a precision error that is fixed with simply increasing mp.dps:

In [31]:
lp, gammap, Egapp = 10, 0, 1/10 

mp.dps = 15 #default value
print("\nWith mp.dps = 15")
mp.nprint(btz1.transition_rate_0(gammap, lp, Egapp, btz1.z_of_TH(1))) 
mp.nprint(btz1.transition_rate_0(gammap, lp, Egapp, btz1.z_of_TH(100))) 

mp.dps = 25 
print("\nWith mp.dps = 25")
mp.nprint(btz1.transition_rate_0(gammap, lp, Egapp, btz1.z_of_TH(1))) 
mp.nprint(btz1.transition_rate_0(gammap, lp, Egapp, btz1.z_of_TH(100))) 



With mp.dps = 15
(-0.00132385, -2.96895e-18)
(-1.32155, 8.62891e-16)

With mp.dps = 25
(0.00150402, 1.02065e-28)
(0.00734508, 2.78888e-27)


In the example above, the normalization even has the wrong sign. Hence, the oscillatory behavior we observe for bad precision settings. 

<div class="alert alert-block alert-warning">
<b>Warning:</b> be careful to not use print() (or the automatic print jupyter does when generating output) when dealing with very small numbers. The best thing to do here is to simply use the function mp.nprint() which will be compatible with the precisions settings in use.
</div>

mp.dps = 200 is enough for the following plots.

In [33]:
mp.dps = 200

x = np.linspace(0, 100, 101)

def func0(l):
    return float(btz1.transition_rate_0(0, l, 1/10, btz1.z_of_TH(100))[0])   
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

def func1(l):
    return float(btz1.transition_rate_0(0, l, 1/10, btz1.z_of_TH(100))[1])   
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))



fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0, name='Re'))
fig.add_trace(go.Scatter(x=x, y=y1, name='Im'))

fig.update_layout(
    title="The l terms for T=100",
    xaxis_title=r"$l$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
)

fig.show()

<IPython.core.display.Javascript object>

In [34]:
mp.dps = 200

x = np.linspace(0, 100, 101)

def func0(l):
    return float(btz1.transition_rate_0(0, l, 1/10, btz1.z_of_TH(1))[0])   
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

def func1(l):
    return float(btz1.transition_rate_0(0, l, 1/10, btz1.z_of_TH(5))[0])   
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

def func2(l):
    return float(btz1.transition_rate_0(0, l, 1/10, btz1.z_of_TH(10))[0])   
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

def func3(l):
    return float(btz1.transition_rate_0(0, l, 1/10, btz1.z_of_TH(50))[0])   
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

def func4(l):
    return float(btz1.transition_rate_0(0, l, 1/10, btz1.z_of_TH(100))[0])   
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))


fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0, name='$T_H=1$'))
fig.add_trace(go.Scatter(x=x, y=y1, name='$T_H=5$'))
fig.add_trace(go.Scatter(x=x, y=y2, name='$T_H=10$'))
fig.add_trace(go.Scatter(x=x, y=y3, name='$T_H=50$'))
fig.add_trace(go.Scatter(x=x, y=y4, name='$T_H=100$'))


fig.update_layout(
    title="l terms of the transition rate for the Ground state on the static BTZ black hole",
    xaxis_title=r"$l_{max}$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Hawking temperatures"
)
fig.show()

<IPython.core.display.Javascript object>

### <span style='color:gray'>Summing up to $l_{max}$ </span>

#### <span style='color:olivedrab'> Ground state with Dirichlet boundary condition:

In [37]:
mp.dps = 200
x = np.linspace(0, 100, 101)
normalization_factor = 2.75

# def func0(l):
#     return float(btz1.transition_rate_0(0, l, 1/10, btz1.z_of_TH(1))[0])   
# vfunc0 = np.vectorize(func0)
# y0 = (vfunc0((x)))

# def func1(l):
#     return float(btz1.transition_rate_0(0, l, 1/10, btz1.z_of_TH(5))[0])   
# vfunc1 = np.vectorize(func1)
# y1 = (vfunc1((x)))

# def func2(l):
#     return float(btz1.transition_rate_0(0, l, 1/10, btz1.z_of_TH(10))[0])   
# vfunc2 = np.vectorize(func2)
# y2 = (vfunc2((x)))

# def func3(l):
#     return float(btz1.transition_rate_0(0, l, 1/10, btz1.z_of_TH(50))[0])   
# vfunc3 = np.vectorize(func3)
# y3 = (vfunc3((x)))

# def func4(l):
#     return float(btz1.transition_rate_0(0, l, 1/10, btz1.z_of_TH(100))[0])   
# vfunc4 = np.vectorize(func4)
# y4 = (vfunc4((x)))


sumy0 = [y0[0]/normalization_factor]
sumy1 = [y1[0]/normalization_factor]
sumy2 = [y2[0]/normalization_factor]
sumy3 = [y3[0]/normalization_factor]
sumy4 = [y4[0]/normalization_factor]
j = 0
while j < len(y0)-1:
    sumy0.append(sumy0[j] + y0[j + 1]/normalization_factor)
    sumy1.append(sumy1[j] + y1[j + 1]/normalization_factor)
    sumy2.append(sumy2[j] + y2[j + 1]/normalization_factor)
    sumy3.append(sumy3[j] + y3[j + 1]/normalization_factor)
    sumy4.append(sumy4[j] + y4[j + 1]/normalization_factor)
    j = j + 1 


fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=sumy0, name='$T_H=1$'))
fig.add_trace(go.Scatter(x=x, y=sumy1, name='$T_H=5$'))
fig.add_trace(go.Scatter(x=x, y=sumy2, name='$T_H=10$'))
fig.add_trace(go.Scatter(x=x, y=sumy3, name='$T_H=50$'))
fig.add_trace(go.Scatter(x=x, y=sumy4, name='$T_H=100$'))


fig.update_layout(
    title="Transition rate for the Ground state summed up to l_max on the static BTZ black hole",
    xaxis_title=r"$l_{max}$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Hawking temperatures"
)

fig.show()

#### <span style='color:olivedrab'>Ground state with Neumann boundary condition:</span>

In [38]:
mp.dps = 200
x = np.linspace(0, 100, 101)
normalization_factor = 2.75

def func0(l):
    return float(btz1.transition_rate_0(pi/2, l, 1/10, btz1.z_of_TH(1))[0])   
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

def func1(l):
    return float(btz1.transition_rate_0(pi/2, l, 1/10, btz1.z_of_TH(5))[0])   
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

def func2(l):
    return float(btz1.transition_rate_0(pi/2, l, 1/10, btz1.z_of_TH(10))[0])   
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

def func3(l):
    return float(btz1.transition_rate_0(pi/2, l, 1/10, btz1.z_of_TH(50))[0])   
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

def func4(l):
    return float(btz1.transition_rate_0(pi/2, l, 1/10, btz1.z_of_TH(100))[0])   
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))


sumy0 = [y0[0]/normalization_factor]
sumy1 = [y1[0]/normalization_factor]
sumy2 = [y2[0]/normalization_factor]
sumy3 = [y3[0]/normalization_factor]
sumy4 = [y4[0]/normalization_factor]
j = 0
while j < len(y0)-1:
    sumy0.append(sumy0[j] + y0[j + 1]/normalization_factor)
    sumy1.append(sumy1[j] + y1[j + 1]/normalization_factor)
    sumy2.append(sumy2[j] + y2[j + 1]/normalization_factor)
    sumy3.append(sumy3[j] + y3[j + 1]/normalization_factor)
    sumy4.append(sumy4[j] + y4[j + 1]/normalization_factor)
    j = j + 1 


fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=sumy0, name='$T_H=1$'))
fig.add_trace(go.Scatter(x=x, y=sumy1, name='$T_H=5$'))
fig.add_trace(go.Scatter(x=x, y=sumy2, name='$T_H=10$'))
fig.add_trace(go.Scatter(x=x, y=sumy3, name='$T_H=50$'))
fig.add_trace(go.Scatter(x=x, y=sumy4, name='$T_H=100$'))


fig.update_layout(
    title="Transition rate for the Ground state summed up to l_max on the static BTZ black hole",
    xaxis_title=r"$l_{max}$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Hawking temperatures"
)

fig.show()

#### <span style='color:olivedrab'>KMS state with Dirichlet boundary condition:</span>

In [39]:
mp.dps = 200
x = np.linspace(0, 100, 101)
#normalization = ?

def func0(l):
    return float(btz1.transition_rate_T(0, l, 1/10, btz1.z_of_TH(1))[0])   
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

def func1(l):
    return float(btz1.transition_rate_T(0, l, 1/10, btz1.z_of_TH(5))[0])   
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

def func2(l):
    return float(btz1.transition_rate_T(0, l, 1/10, btz1.z_of_TH(10))[0])   
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

def func3(l):
    return float(btz1.transition_rate_T(0, l, 1/10, btz1.z_of_TH(50))[0])   
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

def func4(l):
    return float(btz1.transition_rate_T(0, l, 1/10, btz1.z_of_TH(100))[0])   
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))


sumy0 = [y0[0]]
sumy1 = [y1[0]]
sumy2 = [y2[0]]
sumy3 = [y3[0]]
sumy4 = [y4[0]]
j = 0
while j < len(y0)-1:
    sumy0.append(sumy0[j] + y0[j + 1])
    sumy1.append(sumy1[j] + y1[j + 1])
    sumy2.append(sumy2[j] + y2[j + 1])
    sumy3.append(sumy3[j] + y3[j + 1])
    sumy4.append(sumy4[j] + y4[j + 1])
    j = j + 1 


fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=sumy4, name='$T_H=100$'))
fig.add_trace(go.Scatter(x=x, y=sumy3, name='$T_H=50$'))
fig.add_trace(go.Scatter(x=x, y=sumy2, name='$T_H=10$'))
fig.add_trace(go.Scatter(x=x, y=sumy1, name='$T_H=5$'))
fig.add_trace(go.Scatter(x=x, y=sumy0, name='$T_H=1$'))


fig.update_layout(
    title="Transition rate for the KMS state summed up to l_max on the static BTZ black hole",
    xaxis_title=r"$l_{max}$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Hawking temperatures"
)

fig.show()

### <span style='color:gray'>It does look exponentially decreasing</span>

In [40]:
mp.dps = 200

normalization_factor = 2.75

x = np.linspace(0, 100, 101)

def func0(l):
    return float(log(btz1.transition_rate_0(0, l, 1/10, btz1.z_of_TH(1))[0]))/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

def func1(l):
    return float(log(btz1.transition_rate_0(0, l, 1/10, btz1.z_of_TH(5))[0]))/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

def func2(l):
    return float(log(btz1.transition_rate_0(0, l, 1/10, btz1.z_of_TH(10))[0]))/normalization_factor   
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

def func3(l):
    return float(log(btz1.transition_rate_0(0, l, 1/10, btz1.z_of_TH(50))[0]))/normalization_factor  
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

def func4(l):
    return float(log(btz1.transition_rate_0(0, l, 1/10, btz1.z_of_TH(100))[0]))/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))


fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0, name='$T_H=1$'))
fig.add_trace(go.Scatter(x=x, y=y1, name='$T_H=5$'))
fig.add_trace(go.Scatter(x=x, y=y2, name='$T_H=10$'))
fig.add_trace(go.Scatter(x=x, y=y3, name='$T_H=50$'))
fig.add_trace(go.Scatter(x=x, y=y4, name='$T_H=100$'))


fig.update_layout(
    title="log of l terms of the transition rate for the Ground state on the static BTZ black hole",
    xaxis_title=r"$l_{max}$",
    yaxis_title=r"$\log\dot{\mathcal{F}}$",
    legend_title="Hawking temperatures"
)
fig.show()

<IPython.core.display.Javascript object>

#  <span style='color:darkgreen'>M = 0.25</span>

\begin{align}
    & \text{mass of the black hole, } &M&=0.25;\nonumber\\
    & \text{outer horizon, } &r_+&=0.5.\nonumber
\end{align}

In [57]:
btz2 = BTZ(0.25, 0.5)

The following plots are normalizedwith respect to the unit mass case.

## <span style='color:brown'>The $l=0$ term of the transition rate</span>

### <span style='color:gray'>As a function of position z</span>

In [42]:
normalization_factor = 2.75

N = 200
x = np.linspace(1e-5, 1-1e-5, N)

lp, Egapp = 0, 0.1


gamma0 = 0
def func0(p):
    return float(btz2.transition_rate_0(gamma0,lp,Egapp,p)[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

gamma1 = 0.25*np.pi
def func1(p):
    return float(btz2.transition_rate_0(gamma1,lp,Egapp,p)[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

gamma2 = 0.40*np.pi
def func2(p):
    return float(btz2.transition_rate_0(gamma2,lp,Egapp,p)[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

gamma3 = 0.47*np.pi
def func3(p):
    return float(btz2.transition_rate_0(gamma3,lp,Egapp,p)[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

gamma4 = 0.5*np.pi
def func4(p):
    return float(btz2.transition_rate_0(gamma4,lp,Egapp,p)[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))



fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y4, name='Newmann'))
fig.add_trace(go.Scatter(x=x, y=y3, name='Robin 3'))
fig.add_trace(go.Scatter(x=x, y=y2, name='Robin 2'))
fig.add_trace(go.Scatter(x=x, y=y1, name='Robin 1'))
fig.add_trace(go.Scatter(x=x, y=y0, name='Dirichlet'))


fig.update_layout(
    title="Transition rate for the Ground state as a function of position z on the static BTZ black hole",
    xaxis_title=r"$z$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Boundary Conditions"
)

fig.show()

In [44]:
normalization_factor = 280

N = 200
x = np.linspace(1e-2, 1-1e-2, N)

lp, Egapp = 0, 0.1


gamma0 = 0
def func0(p):
    return float(btz2.transition_rate_T(gamma0,lp,Egapp,p)[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

gamma1 = 0.25*np.pi
def func1(p):
    return float(btz2.transition_rate_T(gamma1,lp,Egapp,p)[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

gamma2 = 0.40*np.pi
def func2(p):
    return float(btz2.transition_rate_T(gamma2,lp,Egapp,p)[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

gamma3 = 0.47*np.pi
def func3(p):
    return float(btz2.transition_rate_T(gamma3,lp,Egapp,p)[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

gamma4 = 0.5*np.pi
def func4(p):
    return float(btz2.transition_rate_T(gamma4,lp,Egapp,p)[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y4, name='Newmann'))
fig.add_trace(go.Scatter(x=x, y=y3, name='Robin 3'))
fig.add_trace(go.Scatter(x=x, y=y2, name='Robin 2'))
fig.add_trace(go.Scatter(x=x, y=y1, name='Robin 1'))
fig.add_trace(go.Scatter(x=x, y=y0, name='Dirichlet'))


fig.update_layout(
    title="Transition rate for the KMS state as a function of position z on the static BTZ black hole",
    xaxis_title=r"$z$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Boundary Conditions"
)

fig.show()

### <span style='color:gray'>As a function of the Hawking temperature</span>

In [45]:
normalization_factor = 2.75

N = 200
x = np.linspace(1e-3, 1-1e-3, N)

lp, Egapp = 0, 0.1


gamma0 = 0
def func0(T):
    return float(btz2.transition_rate_0(gamma0,lp,Egapp,btz2.z_of_TH(T))[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

gamma1 = 0.25*np.pi
def func1(T):
    return float(btz2.transition_rate_0(gamma1,lp,Egapp,btz2.z_of_TH(T))[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

gamma2 = 0.40*np.pi
def func2(T):
    return float(btz2.transition_rate_0(gamma2,lp,Egapp,btz2.z_of_TH(T))[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

gamma3 = 0.47*np.pi
def func3(T):
    return float(btz2.transition_rate_0(gamma3,lp,Egapp,btz2.z_of_TH(T))[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

gamma4 = 0.5*np.pi
def func4(T):
    return float(btz2.transition_rate_0(gamma4,lp,Egapp,btz2.z_of_TH(T))[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y4, name='Newmann'))
fig.add_trace(go.Scatter(x=x, y=y3, name='Robin 3'))
fig.add_trace(go.Scatter(x=x, y=y2, name='Robin 2'))
fig.add_trace(go.Scatter(x=x, y=y1, name='Robin 1'))
fig.add_trace(go.Scatter(x=x, y=y0, name='Dirichlet'))


fig.update_layout(
    title="Transition rate for the Ground state as a function of the Hawking temperature on the static BTZ black hole",
    xaxis_title=r"$T_H$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Boundary Conditions"
)

fig.show()

In [59]:
normalization_factor = 140

N = 200
x = np.linspace(1e-2, 1-1e-2, N)

lp, Egapp = 0, 0.1


gamma0 = 0
def func0(T):
    return float(btz2.transition_rate_T(gamma0,lp,Egapp,btz2.z_of_TH(T))[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

gamma1 = 0.25*np.pi
def func1(T):
    return float(btz2.transition_rate_T(gamma1,lp,Egapp,btz2.z_of_TH(T))[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

gamma2 = 0.40*np.pi
def func2(T):
    return float(btz2.transition_rate_T(gamma2,lp,Egapp,btz2.z_of_TH(T))[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

gamma3 = 0.47*np.pi
def func3(T):
    return float(btz2.transition_rate_T(gamma3,lp,Egapp,btz2.z_of_TH(T))[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

gamma4 = 0.5*np.pi
def func4(T):
    return float(btz2.transition_rate_T(gamma4,lp,Egapp,btz2.z_of_TH(T))[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y4, name='Newmann'))
fig.add_trace(go.Scatter(x=x, y=y3, name='Robin 3'))
fig.add_trace(go.Scatter(x=x, y=y2, name='Robin 2'))
fig.add_trace(go.Scatter(x=x, y=y1, name='Robin 1'))
fig.add_trace(go.Scatter(x=x, y=y0, name='Dirichlet'))


fig.update_layout(
    title="Transition rate for the KMS state as a function of the Hawking temperature on the static BTZ black hole",
    xaxis_title=r"$T_H$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Boundary Conditions"
)

fig.show()

### <span style='color:gray'>As a function of the energy gap</span>

In [60]:
normalization_factor = 4.86

N = 200
x = np.linspace(1e-3, 5, N)

lp, zp = 0, 0.5


gamma0 = 0
def func0(Egap):
    return float(btz2.transition_rate_0(gamma0,lp,Egap,zp)[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

gamma1 = 0.25*np.pi
def func1(Egap):
    return float(btz2.transition_rate_0(gamma1,lp,Egap,zp)[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

gamma2 = 0.40*np.pi
def func2(Egap):
    return float(btz2.transition_rate_0(gamma2,lp,Egap,zp)[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

gamma3 = 0.47*np.pi
def func3(Egap):
    return float(btz2.transition_rate_0(gamma3,lp,Egap,zp)[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

gamma4 = 0.5*np.pi
def func4(Egap):
    return float(btz2.transition_rate_0(gamma4,lp,Egap,zp)[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y4, name='Newmann'))
fig.add_trace(go.Scatter(x=x, y=y3, name='Robin 3'))
fig.add_trace(go.Scatter(x=x, y=y2, name='Robin 2'))
fig.add_trace(go.Scatter(x=x, y=y1, name='Robin 1'))
fig.add_trace(go.Scatter(x=x, y=y0, name='Dirichlet'))


fig.update_layout(
    title="Transition rate for the Ground state as a function of the energy gap on the static BTZ black hole",
    xaxis_title=r"$E_{gap}$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Boundary Conditions"
)

fig.show()

In [61]:
normalization_factor = 9.31

N = 200
x = np.linspace(1e-3, 1, N)

lp, zp = 0, 0.5


gamma0 = 0
def func0(Egap):
    return float(btz2.transition_rate_T(gamma0,lp,Egap,zp)[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

gamma1 = 0.25*np.pi
def func1(Egap):
    return float(btz2.transition_rate_T(gamma1,lp,Egap,zp)[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

gamma2 = 0.40*np.pi
def func2(Egap):
    return float(btz2.transition_rate_T(gamma2,lp,Egap,zp)[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

gamma3 = 0.47*np.pi
def func3(Egap):
    return float(btz2.transition_rate_T(gamma3,lp,Egap,zp)[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

gamma4 = 0.5*np.pi
def func4(Egap):
    return float(btz2.transition_rate_T(gamma4,lp,Egap,zp)[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y4, name='Newmann'))
fig.add_trace(go.Scatter(x=x, y=y3, name='Robin 3'))
fig.add_trace(go.Scatter(x=x, y=y2, name='Robin 2'))
fig.add_trace(go.Scatter(x=x, y=y1, name='Robin 1'))
fig.add_trace(go.Scatter(x=x, y=y0, name='Dirichlet'))


fig.update_layout(
    title="Transition rate for the KMS state as a function of the energy gap on the static BTZ black hole",
    xaxis_title=r"$E_{gap}$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Boundary Conditions"
)

fig.show()

## <span style='color:brown'>First few different $l$ terms</span>

### <span style='color:gray'>Dirichlet boundary condition</span>

In [66]:
normalization_factor = 2.75

mp.dps =200
N = 200
x = np.linspace(1e-3, 1-1e-3, N)

Egapp, gamma0 = 0.1, 0


l0 = 0
def func0(z):
    return float(btz2.transition_rate_0(gamma0,l0,Egapp,z)[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

l1 = 1
def func1(z):
    return float(btz2.transition_rate_0(gamma0,l1,Egapp,z)[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

l2 = 2
def func2(z):
    return float(btz2.transition_rate_0(gamma0,l2,Egapp,z)[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

l3 = 3
def func3(z):
    return float(btz2.transition_rate_0(gamma0,l3,Egapp,z)[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

l4 = 4
def func4(z):
    return float(btz2.transition_rate_0(gamma0,l4,Egapp,z)[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0, name=r'$l=0$'))
fig.add_trace(go.Scatter(x=x, y=y1, name=r'$l=1$'))
fig.add_trace(go.Scatter(x=x, y=y2, name=r'$l=2$'))
fig.add_trace(go.Scatter(x=x, y=y3, name=r'$l=3$'))
fig.add_trace(go.Scatter(x=x, y=y4, name=r'$l=4$'))


fig.update_layout(
    title="Contributions to the transition rate for the Ground state with Dirichlet b.c. on the static BTZ black hole",
    xaxis_title=r"$z$",
    yaxis_title=r"$\dot{\mathcal{F}}$"
)

fig.show()

In [67]:
normalization_factor = 2.75

mp.dps = 200
N = 200
x = np.linspace(1e-3, 5, N)

Egapp, gamma0 = 0.1, 0


l0 = 0
def func0(T):
    return float(btz2.transition_rate_0(gamma0,l0,Egapp,btz2.z_of_TH(T))[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

l1 = 1
def func1(T):
    return float(btz2.transition_rate_0(gamma0,l1,Egapp,btz2.z_of_TH(T))[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

l2 = 2
def func2(T):
    return float(btz2.transition_rate_0(gamma0,l2,Egapp,btz2.z_of_TH(T))[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

l3 = 3
def func3(T):
    return float(btz2.transition_rate_0(gamma0,l3,Egapp,btz2.z_of_TH(T))[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

l4 = 4
def func4(T):
    return float(btz2.transition_rate_0(gamma0,l4,Egapp,btz2.z_of_TH(T))[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0, name=r'$l=0$'))
fig.add_trace(go.Scatter(x=x, y=y1, name=r'$l=1$'))
fig.add_trace(go.Scatter(x=x, y=y2, name=r'$l=2$'))
fig.add_trace(go.Scatter(x=x, y=y3, name=r'$l=3$'))
fig.add_trace(go.Scatter(x=x, y=y4, name=r'$l=4$'))


fig.update_layout(
    title="Contributions to the transition rate for the Ground state with Dirichlet b.c. on the static BTZ black hole",
    xaxis_title=r"$T_H$",
    yaxis_title=r"$\dot{\mathcal{F}}$"
)

fig.show()

### <span style='color:gray'>For Neumann boundary condition</span>

In [68]:
normalization_factor = 2.75

mp.dps = 200
N = 200
x = np.linspace(1e-3, 1-1e-3, N)

Egapp, gamma4 = 0.1, np.pi/2


l0 = 0
def func0(z):
    return float(btz2.transition_rate_0(gamma4,l0,Egapp,z)[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

l1 = 1
def func1(z):
    return float(btz2.transition_rate_0(gamma4,l1,Egapp,z)[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

l2 = 2
def func2(z):
    return float(btz2.transition_rate_0(gamma4,l2,Egapp,z)[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

l3 = 3
def func3(z):
    return float(btz2.transition_rate_0(gamma4,l3,Egapp,z)[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

l4 = 4
def func4(z):
    return float(btz2.transition_rate_0(gamma4,l4,Egapp,z)[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0, name=r'$l=0$'))
fig.add_trace(go.Scatter(x=x, y=y1, name=r'$l=1$'))
fig.add_trace(go.Scatter(x=x, y=y2, name=r'$l=2$'))
fig.add_trace(go.Scatter(x=x, y=y3, name=r'$l=3$'))
fig.add_trace(go.Scatter(x=x, y=y4, name=r'$l=4$'))


fig.update_layout(
    title="Contributions to the transition rate for the Ground state with Neumann b.c. on the static BTZ black hole",
    xaxis_title=r"$z$",
    yaxis_title=r"$\dot{\mathcal{F}}$"
)

fig.show()

In [69]:
normalization_factor = 2.75

mp.dps = 200
N = 250
x = np.linspace(1e-3,5, N)

Egapp, gamma4 = 0.1, np.pi/2


l0 = 0
def func0(T):
    return float(btz2.transition_rate_0(gamma4,l0,Egapp,btz2.z_of_TH(T))[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

l1 = 1
def func1(T):
    return float(btz2.transition_rate_0(gamma4,l1,Egapp,btz2.z_of_TH(T))[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

l2 = 2
def func2(T):
    return float(btz2.transition_rate_0(gamma4,l2,Egapp,btz2.z_of_TH(T))[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

l3 = 3
def func3(T):
    return float(btz2.transition_rate_0(gamma4,l3,Egapp,btz2.z_of_TH(T))[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

l4 = 4
def func4(T):
    return float(btz2.transition_rate_0(gamma4,l4,Egapp,btz2.z_of_TH(T))[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0, name=r'$l=0$'))
fig.add_trace(go.Scatter(x=x, y=y1, name=r'$l=1$'))
fig.add_trace(go.Scatter(x=x, y=y2, name=r'$l=2$'))
fig.add_trace(go.Scatter(x=x, y=y3, name=r'$l=3$'))
fig.add_trace(go.Scatter(x=x, y=y4, name=r'$l=4$'))


fig.update_layout(
    title="Contributions to the transition rate for the Ground state with Neumann b.c. on the static BTZ black hole",
    xaxis_title=r"$T_H$",
    yaxis_title=r"$\dot{\mathcal{F}}$"
)

fig.show()

## <span style='color:brown'>Sum in $l$</span>

### <span style='color:gray'>Precision settings exploration</span>

mp.dps = 300 is enough for the following plots.

In [70]:
mp.dps = 300

normalization_factor = 2.75

x = np.linspace(0, 100, 101)

def func0(l):
    return float(btz2.transition_rate_0(0, l,1/10, btz2.z_of_TH(100))[0])   
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

def func1(l):
    return float(btz2.transition_rate_0(0, l, 1/10, btz2.z_of_TH(100))[1])   
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))



fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0, name='Re'))
fig.add_trace(go.Scatter(x=x, y=y1, name='Im'))

fig.update_layout(
    title="The l terms for T=100",
    xaxis_title=r"$l$",
    yaxis_title=r"$\dot{\mathcal{F}}$"
)

fig.show()

<IPython.core.display.Javascript object>

In [71]:
mp.dps = 300

normalization_factor = 2.75

x = np.linspace(0, 100, 101)

def func0(l):
    return float(btz2.transition_rate_0(0, l, 1/10, btz2.z_of_TH(1))[0])   
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

def func1(l):
    return float(btz2.transition_rate_0(0, l, 1/10, btz2.z_of_TH(5))[0])   
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

def func2(l):
    return float(btz2.transition_rate_0(0, l, 1/10, btz2.z_of_TH(10))[0])   
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

def func3(l):
    return float(btz2.transition_rate_0(0, l, 1/10, btz2.z_of_TH(50))[0])   
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

def func4(l):
    return float(btz2.transition_rate_0(0, l, 1/10, btz2.z_of_TH(100))[0])   
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))


fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0, name='$T_H=1$'))
fig.add_trace(go.Scatter(x=x, y=y1, name='$T_H=5$'))
fig.add_trace(go.Scatter(x=x, y=y2, name='$T_H=10$'))
fig.add_trace(go.Scatter(x=x, y=y3, name='$T_H=50$'))
fig.add_trace(go.Scatter(x=x, y=y4, name='$T_H=100$'))


fig.update_layout(
    title="l terms of the transition rate for the Ground state on the static BTZ black hole.",
    xaxis_title=r"$l_{max}$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Hawking temperatures"
)
fig.show()

<IPython.core.display.Javascript object>

### <span style='color:gray'>Summing up to $l_{max}$ </span>

####  <span style='color:olivedrab'> Ground state with Dirichlet boundary condition:</span>

In [72]:
x = np.linspace(0, 100, 101)
mp.dps = 300
normalization_factor = 2.75

def func0(l):
    return float(btz2.transition_rate_0(0, l, 1/10, btz2.z_of_TH(1))[0])   
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

def func1(l):
    return float(btz2.transition_rate_0(0, l, 1/10, btz2.z_of_TH(5))[0])   
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

def func2(l):
    return float(btz2.transition_rate_0(0, l, 1/10, btz2.z_of_TH(10))[0])   
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

def func3(l):
    return float(btz2.transition_rate_0(0, l, 1/10, btz2.z_of_TH(50))[0])   
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

def func4(l):
    return float(btz2.transition_rate_0(0, l, 1/10, btz2.z_of_TH(100))[0])   
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))


sumy0 = [y0[0]/normalization_factor]
sumy1 = [y1[0]/normalization_factor]
sumy2 = [y2[0]/normalization_factor]
sumy3 = [y3[0]/normalization_factor]
sumy4 = [y4[0]/normalization_factor]
j = 0
while j < len(y0)-1:
    sumy0.append(sumy0[j] + y0[j + 1]/normalization_factor)
    sumy1.append(sumy1[j] + y1[j + 1]/normalization_factor)
    sumy2.append(sumy2[j] + y2[j + 1]/normalization_factor)
    sumy3.append(sumy3[j] + y3[j + 1]/normalization_factor)
    sumy4.append(sumy4[j] + y4[j + 1]/normalization_factor)
    j = j + 1 


fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=sumy0, name='$T_H=1$'))
fig.add_trace(go.Scatter(x=x, y=sumy1, name='$T_H=5$'))
fig.add_trace(go.Scatter(x=x, y=sumy2, name='$T_H=10$'))
fig.add_trace(go.Scatter(x=x, y=sumy3, name='$T_H=50$'))
fig.add_trace(go.Scatter(x=x, y=sumy4, name='$T_H=100$'))


fig.update_layout(
    title="Transition rate for the Ground state summed up to l_max on the static BTZ black hole.",
    xaxis_title=r"$l_{max}$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Hawking temperatures"
)

fig.show()

#### <span style='color:olivedrab'>  Ground state with Neumann boundary condition:</span>

In [73]:
x = np.linspace(0, 100, 101)
mp.dps = 300
normalization_factor = 2.75

def func0(l):
    return float(btz2.transition_rate_0(pi/2, l, 1/10, btz2.z_of_TH(1))[0])   
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

def func1(l):
    return float(btz2.transition_rate_0(pi/2, l, 1/10, btz2.z_of_TH(5))[0])   
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

def func2(l):
    return float(btz2.transition_rate_0(pi/2, l, 1/10, btz2.z_of_TH(10))[0])   
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

def func3(l):
    return float(btz2.transition_rate_0(pi/2, l, 1/10, btz2.z_of_TH(50))[0])   
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

def func4(l):
    return float(btz2.transition_rate_0(pi/2, l, 1/10, btz2.z_of_TH(100))[0])   
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))


sumy0 = [y0[0]/normalization_factor]
sumy1 = [y1[0]/normalization_factor]
sumy2 = [y2[0]/normalization_factor]
sumy3 = [y3[0]/normalization_factor]
sumy4 = [y4[0]/normalization_factor]
j = 0
while j < len(y0)-1:
    sumy0.append(sumy0[j] + y0[j + 1]/normalization_factor)
    sumy1.append(sumy1[j] + y1[j + 1]/normalization_factor)
    sumy2.append(sumy2[j] + y2[j + 1]/normalization_factor)
    sumy3.append(sumy3[j] + y3[j + 1]/normalization_factor)
    sumy4.append(sumy4[j] + y4[j + 1]/normalization_factor)
    j = j + 1 


fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=sumy0, name='$T_H=1$'))
fig.add_trace(go.Scatter(x=x, y=sumy1, name='$T_H=5$'))
fig.add_trace(go.Scatter(x=x, y=sumy2, name='$T_H=10$'))
fig.add_trace(go.Scatter(x=x, y=sumy3, name='$T_H=50$'))
fig.add_trace(go.Scatter(x=x, y=sumy4, name='$T_H=100$'))


fig.update_layout(
    title="Transition rate for the Ground state summed up to l_max on the static BTZ black hole",
    xaxis_title=r"$l_{max}$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Hawking temperatures"
)

fig.show()

####   <span style='color:olivedrab'> KMS state with Dirichlet boundary condition</span>

In [75]:
x = np.linspace(0, 100, 101)
mp.dps = 300
normalization_factor = 324000

def func0(l):
    return float(btz2.transition_rate_T(0, l, 1/10, btz2.z_of_TH(1))[0])   
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

def func1(l):
    return float(btz2.transition_rate_T(0, l, 1/10, btz2.z_of_TH(5))[0])   
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

def func2(l):
    return float(btz2.transition_rate_T(0, l, 1/10, btz2.z_of_TH(10))[0])   
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

def func3(l):
    return float(btz2.transition_rate_T(0, l, 1/10, btz2.z_of_TH(50))[0])   
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

def func4(l):
    return float(btz2.transition_rate_T(0, l, 1/10, btz2.z_of_TH(100))[0])   
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))


sumy0 = [y0[0]/normalization_factor]
sumy1 = [y1[0]/normalization_factor]
sumy2 = [y2[0]/normalization_factor]
sumy3 = [y3[0]/normalization_factor]
sumy4 = [y4[0]/normalization_factor]
j = 0
while j < len(y0)-1:
    sumy0.append(sumy0[j] + y0[j + 1]/normalization_factor)
    sumy1.append(sumy1[j] + y1[j + 1]/normalization_factor)
    sumy2.append(sumy2[j] + y2[j + 1]/normalization_factor)
    sumy3.append(sumy3[j] + y3[j + 1]/normalization_factor)
    sumy4.append(sumy4[j] + y4[j + 1]/normalization_factor)
    j = j + 1 


fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=sumy4, name='$T_H=100$'))
fig.add_trace(go.Scatter(x=x, y=sumy3, name='$T_H=50$'))
fig.add_trace(go.Scatter(x=x, y=sumy2, name='$T_H=10$'))
fig.add_trace(go.Scatter(x=x, y=sumy1, name='$T_H=5$'))
fig.add_trace(go.Scatter(x=x, y=sumy0, name='$T_H=1$'))


fig.update_layout(
    title="Transition rate for the KMS state summed up to l_max on the static BTZ black hole",
    xaxis_title=r"$l_{max}$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Hawking temperatures"
)

fig.show()

### <span style='color:gray'>It does look exponentially decreasing</span>

In [76]:
mp.dps = 300
normalization_factor = 2.75

x = np.linspace(0, 100, 101)

def func0(l):
    return float(log(btz2.transition_rate_0(0, l, 1/10, btz2.z_of_TH(1))[0]))/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

def func1(l):
    return float(log(btz2.transition_rate_0(0, l, 1/10, btz2.z_of_TH(5))[0]))/normalization_factor   
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

def func2(l):
    return float(log(btz2.transition_rate_0(0, l, 1/10, btz2.z_of_TH(10))[0]))/normalization_factor 
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

def func3(l):
    return float(log(btz2.transition_rate_0(0, l, 1/10, btz2.z_of_TH(50))[0]))/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

def func4(l):
    return float(log(btz2.transition_rate_0(0, l, 1/10, btz2.z_of_TH(100))[0]))/normalization_factor 
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))


fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0, name='$T_H=1$'))
fig.add_trace(go.Scatter(x=x, y=y1, name='$T_H=5$'))
fig.add_trace(go.Scatter(x=x, y=y2, name='$T_H=10$'))
fig.add_trace(go.Scatter(x=x, y=y3, name='$T_H=50$'))
fig.add_trace(go.Scatter(x=x, y=y4, name='$T_H=100$'))


fig.update_layout(
    title="log of l terms of the transition rate for the Ground state on the static BTZ black hole",
    xaxis_title=r"$l_{max}$",
    yaxis_title=r"$\log\dot{\mathcal{F}}$",
    legend_title="Hawking temperatures"
)
fig.show()

<IPython.core.display.Javascript object>

#  <span style='color:darkgreen'>M = 0.01</span>

\begin{align}
    & \text{mass of the black hole, } &M&=0.01;\nonumber\\
    & \text{outer horizon, } &r_+&=0.1.\nonumber
\end{align}

In [62]:
btz3 = BTZ(0.01, 0.1)

The following plots are normalizedwith respect to the unit mass case.

## <span style='color:brown'>The $l=0$ term of the transition rate</span>

### <span style='color:gray'>As a function of position z</span>

In [77]:
normalization_factor = 2.75

N = 200
x = np.linspace(1e-3, 1-1e-3, N)

lp, Egapp = 0, 0.1


gamma0 = 0
def func0(p):
    return float(btz3.transition_rate_0(gamma0,lp,Egapp,p)[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

gamma1 = 0.25*pi
def func1(p):
    return float(btz3.transition_rate_0(gamma1,lp,Egapp,p)[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

gamma2 = 0.40*pi
def func2(p):
    return float(btz3.transition_rate_0(gamma2,lp,Egapp,p)[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

gamma3 = 0.47*pi
def func3(p):
    return float(btz3.transition_rate_0(gamma3,lp,Egapp,p)[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

gamma4 = 0.5*pi
def func4(p):
    return float(btz3.transition_rate_0(gamma4,lp,Egapp,p)[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y4, name='Newmann'))
fig.add_trace(go.Scatter(x=x, y=y3, name='Robin 3'))
fig.add_trace(go.Scatter(x=x, y=y2, name='Robin 2'))
fig.add_trace(go.Scatter(x=x, y=y1, name='Robin 1'))
fig.add_trace(go.Scatter(x=x, y=y0, name='Dirichlet'))


fig.update_layout(
    title="Transition rate for the Ground state as a function of position z on the static BTZ black hole",
    xaxis_title=r"$z$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Boundary Conditions"
)

fig.show()

In [80]:
normalization_factor = 1400

N = 200
x = np.linspace(1e-2, 1-1e-2, N)

lp, Egapp = 0, 0.1


gamma0 = 0
def func0(p):
    return float(btz3.transition_rate_T(gamma0,lp,Egapp,p)[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

gamma1 = 0.25*pi
def func1(p):
    return float(btz3.transition_rate_T(gamma1,lp,Egapp,p)[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

gamma2 = 0.40*pi
def func2(p):
    return float(btz3.transition_rate_T(gamma2,lp,Egapp,p)[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

gamma3 = 0.47*pi
def func3(p):
    return float(btz3.transition_rate_T(gamma3,lp,Egapp,p)[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

gamma4 = 0.5*pi
def func4(p):
    return float(btz3.transition_rate_T(gamma4,lp,Egapp,p)[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y4, name='Newmann'))
fig.add_trace(go.Scatter(x=x, y=y3, name='Robin 3'))
fig.add_trace(go.Scatter(x=x, y=y2, name='Robin 2'))
fig.add_trace(go.Scatter(x=x, y=y1, name='Robin 1'))
fig.add_trace(go.Scatter(x=x, y=y0, name='Dirichlet'))


fig.update_layout(
    title="Transition rate for the KMS state as a function of position z on the static BTZ black hole",
    xaxis_title=r"$z$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Boundary Conditions"
)

fig.show()

### <span style='color:gray'>As a function of the Hawking temperature</span>

In [79]:
normalization_factor = 2.75

N = 200
x = np.linspace(1e-3, 1-1e-3, N)

lp, Egapp = 0, 0.1


gamma0 = 0
def func0(T):
    return float(btz3.transition_rate_0(gamma0,lp,Egapp,btz3.z_of_TH(T))[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

gamma1 = 0.25*np.pi
def func1(T):
    return float(btz3.transition_rate_0(gamma1,lp,Egapp,btz3.z_of_TH(T))[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

gamma2 = 0.40*np.pi
def func2(T):
    return float(btz3.transition_rate_0(gamma2,lp,Egapp,btz3.z_of_TH(T))[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

gamma3 = 0.47*np.pi
def func3(T):
    return float(btz3.transition_rate_0(gamma3,lp,Egapp,btz3.z_of_TH(T))[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

gamma4 = 0.5*np.pi
def func4(T):
    return float(btz3.transition_rate_0(gamma4,lp,Egapp,btz3.z_of_TH(T))[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y4, name='Newmann'))
fig.add_trace(go.Scatter(x=x, y=y3, name='Robin 3'))
fig.add_trace(go.Scatter(x=x, y=y2, name='Robin 2'))
fig.add_trace(go.Scatter(x=x, y=y1, name='Robin 1'))
fig.add_trace(go.Scatter(x=x, y=y0, name='Dirichlet'))


fig.update_layout(
    title="Transition rate for the Ground state as a function of the Hawking temperature on the static BTZ black hole",
    xaxis_title=r"$T_H$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Boundary Conditions"
)

fig.show()

In [65]:
normalization_factor = 6000

N = 200
x = np.linspace(1e-2, 5, N)

lp, Egapp = 0, 0.1


gamma0 = 0
def func0(T):
    return float(btz3.transition_rate_T(gamma0,lp,Egapp,btz3.z_of_TH(T))[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

gamma1 = 0.25*np.pi
def func1(T):
    return float(btz3.transition_rate_T(gamma1,lp,Egapp,btz3.z_of_TH(T))[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

gamma2 = 0.40*np.pi
def func2(T):
    return float(btz3.transition_rate_T(gamma2,lp,Egapp,btz3.z_of_TH(T))[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

gamma3 = 0.47*np.pi
def func3(T):
    return float(btz3.transition_rate_T(gamma3,lp,Egapp,btz3.z_of_TH(T))[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

gamma4 = 0.5*np.pi
def func4(T):
    return float(btz3.transition_rate_T(gamma4,lp,Egapp,btz3.z_of_TH(T))[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y4, name='Newmann'))
fig.add_trace(go.Scatter(x=x, y=y3, name='Robin 3'))
fig.add_trace(go.Scatter(x=x, y=y2, name='Robin 2'))
fig.add_trace(go.Scatter(x=x, y=y1, name='Robin 1'))
fig.add_trace(go.Scatter(x=x, y=y0, name='Dirichlet'))


fig.update_layout(
    title="Transition rate for the KMS state as a function of the Hawking temperature on the static BTZ black hole",
    xaxis_title=r"$T_H$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Boundary Conditions"
#     ,font=dict(
#         family="Helvetica",
#         size=18,
#         color="RebeccaPurple"
#     )
)

fig.show()

### <span style='color:gray'>As a function of the energy gap</span>

In [84]:
normalization_factor = 4.86

N = 200
x = np.linspace(1e-3, 5, N)

lp, zp = 0, 0.5


gamma0 = 0
def func0(Egap):
    return float(btz3.transition_rate_0(gamma0,lp,Egap,zp)[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

gamma1 = 0.25*np.pi
def func1(Egap):
    return float(btz3.transition_rate_0(gamma1,lp,Egap,zp)[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

gamma2 = 0.40*np.pi
def func2(Egap):
    return float(btz3.transition_rate_0(gamma2,lp,Egap,zp)[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

gamma3 = 0.47*np.pi
def func3(Egap):
    return float(btz3.transition_rate_0(gamma3,lp,Egap,zp)[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

gamma4 = 0.5*np.pi
def func4(Egap):
    return float(btz3.transition_rate_0(gamma4,lp,Egap,zp)[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y4, name='Newmann'))
fig.add_trace(go.Scatter(x=x, y=y3, name='Robin 3'))
fig.add_trace(go.Scatter(x=x, y=y2, name='Robin 2'))
fig.add_trace(go.Scatter(x=x, y=y1, name='Robin 1'))
fig.add_trace(go.Scatter(x=x, y=y0, name='Dirichlet'))


fig.update_layout(
    title="Transition rate for the Ground state as a function of the energy gap on the static BTZ black hole",
    xaxis_title=r"$E_{gap}$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Boundary Conditions"
)

fig.show()

In [86]:
normalization_factor = 46.6

N = 200
x = np.linspace(1e-3, 1, N)

lp, zp = 0, 0.5


gamma0 = 0
def func0(Egap):
    return float(btz3.transition_rate_T(gamma0,lp,Egap,zp)[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

gamma1 = 0.25*np.pi
def func1(Egap):
    return float(btz3.transition_rate_T(gamma1,lp,Egap,zp)[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

gamma2 = 0.40*np.pi
def func2(Egap):
    return float(btz3.transition_rate_T(gamma2,lp,Egap,zp)[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

gamma3 = 0.47*np.pi
def func3(Egap):
    return float(btz3.transition_rate_T(gamma3,lp,Egap,zp)[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

gamma4 = 0.5*np.pi
def func4(Egap):
    return float(btz3.transition_rate_T(gamma4,lp,Egap,zp)[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y4, name='Newmann'))
fig.add_trace(go.Scatter(x=x, y=y3, name='Robin 3'))
fig.add_trace(go.Scatter(x=x, y=y2, name='Robin 2'))
fig.add_trace(go.Scatter(x=x, y=y1, name='Robin 1'))
fig.add_trace(go.Scatter(x=x, y=y0, name='Dirichlet'))


fig.update_layout(
    title="Transition rate for the KMS state as a function of the energy gap on the static BTZ black hole",
    xaxis_title=r"$E_{gap}$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Boundary Conditions"
)

fig.show()

## <span style='color:brown'>First few different $l$ terms</span>

### <span style='color:gray'>Dirichlet boundary condition</span>

In [87]:
mp.dps = 200

normalization_factor = 2.75

N = 200
x = np.linspace(1e-3, 1-1e-3, N)

Egapp, gamma0 = 0.1, 0


l0 = 0
def func0(z):
    return float(btz3.transition_rate_0(gamma0,l0,Egapp,z)[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

l1 = 1
def func1(z):
    return float(btz3.transition_rate_0(gamma0,l1,Egapp,z)[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

l2 = 2
def func2(z):
    return float(btz3.transition_rate_0(gamma0,l2,Egapp,z)[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

l3 = 3
def func3(z):
    return float(btz3.transition_rate_0(gamma0,l3,Egapp,z)[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

l4 = 4
def func4(z):
    return float(btz3.transition_rate_0(gamma0,l4,Egapp,z)[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0, name=r'$l=0$'))
fig.add_trace(go.Scatter(x=x, y=y1, name=r'$l=1$'))
fig.add_trace(go.Scatter(x=x, y=y2, name=r'$l=2$'))
fig.add_trace(go.Scatter(x=x, y=y3, name=r'$l=3$'))
fig.add_trace(go.Scatter(x=x, y=y4, name=r'$l=4$'))


fig.update_layout(
    title="Contributions to the transition rate for the Ground state with Dirichlet b.c. on the static BTZ black hole",
    xaxis_title=r"$z$",
    yaxis_title=r"$\dot{\mathcal{F}}$"
)

fig.show()

In [88]:
mp.dps = 200

normalization_factor = 2.75

N = 200
x = np.linspace(1e-3, 5, N)

Egapp, gamma0 = 0.1, 0


l0 = 0
def func0(T):
    return float(btz3.transition_rate_0(gamma0,l0,Egapp,btz3.z_of_TH(T))[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

l1 = 1
def func1(T):
    return float(btz3.transition_rate_0(gamma0,l1,Egapp,btz3.z_of_TH(T))[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

l2 = 2
def func2(T):
    return float(btz3.transition_rate_0(gamma0,l2,Egapp,btz3.z_of_TH(T))[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

l3 = 3
def func3(T):
    return float(btz3.transition_rate_0(gamma0,l3,Egapp,btz3.z_of_TH(T))[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

l4 = 4
def func4(T):
    return float(btz3.transition_rate_0(gamma0,l4,Egapp,btz3.z_of_TH(T))[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0, name=r'$l=0$'))
fig.add_trace(go.Scatter(x=x, y=y1, name=r'$l=1$'))
fig.add_trace(go.Scatter(x=x, y=y2, name=r'$l=2$'))
fig.add_trace(go.Scatter(x=x, y=y3, name=r'$l=3$'))
fig.add_trace(go.Scatter(x=x, y=y4, name=r'$l=4$'))


fig.update_layout(
    title="Contributions to the transition rate for the Ground state with Dirichlet b.c. on the static BTZ black hole",
    xaxis_title=r"$T_H$",
    yaxis_title=r"$\dot{\mathcal{F}}$"
)

fig.show()

### <span style='color:gray'>For Neumann boundary condition</span>

In [89]:
mp.dps = 200

normalization_factor = 2.75

N = 200
x = np.linspace(1e-3, 1-1e-3, N)

Egapp, gamma4 = 0.1, pi/2


l0 = 0
def func0(z):
    return float(btz3.transition_rate_0(gamma4,l0,Egapp,z)[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

l1 = 1
def func1(z):
    return float(btz3.transition_rate_0(gamma4,l1,Egapp,z)[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

l2 = 2
def func2(z):
    return float(btz3.transition_rate_0(gamma4,l2,Egapp,z)[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

l3 = 3
def func3(z):
    return float(btz3.transition_rate_0(gamma4,l3,Egapp,z)[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

l4 = 4
def func4(z):
    return float(btz3.transition_rate_0(gamma4,l4,Egapp,z)[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0, name=r'$l=0$'))
fig.add_trace(go.Scatter(x=x, y=y1, name=r'$l=1$'))
fig.add_trace(go.Scatter(x=x, y=y2, name=r'$l=2$'))
fig.add_trace(go.Scatter(x=x, y=y3, name=r'$l=3$'))
fig.add_trace(go.Scatter(x=x, y=y4, name=r'$l=4$'))


fig.update_layout(
    title="Contributions to the transition rate for the Ground state with Neumann b.c. on the static BTZ black hole",
    xaxis_title=r"$z$",
    yaxis_title=r"$\dot{\mathcal{F}}$"
)

fig.show()

In [90]:
mp.dps = 200

normalization_factor = 2.75

N = 250
x = np.linspace(1e-3,5, N)

Egapp, gamma4 = 0.1, np.pi/2


l0 = 0
def func0(T):
    return float(btz3.transition_rate_0(gamma4,l0,Egapp,btz3.z_of_TH(T))[0])/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

l1 = 1
def func1(T):
    return float(btz3.transition_rate_0(gamma4,l1,Egapp,btz3.z_of_TH(T))[0])/normalization_factor
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

l2 = 2
def func2(T):
    return float(btz3.transition_rate_0(gamma4,l2,Egapp,btz3.z_of_TH(T))[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

l3 = 3
def func3(T):
    return float(btz3.transition_rate_0(gamma4,l3,Egapp,btz3.z_of_TH(T))[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

l4 = 4
def func4(T):
    return float(btz3.transition_rate_0(gamma4,l4,Egapp,btz3.z_of_TH(T))[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))




fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0, name=r'$l=0$'))
fig.add_trace(go.Scatter(x=x, y=y1, name=r'$l=1$'))
fig.add_trace(go.Scatter(x=x, y=y2, name=r'$l=2$'))
fig.add_trace(go.Scatter(x=x, y=y3, name=r'$l=3$'))
fig.add_trace(go.Scatter(x=x, y=y4, name=r'$l=4$'))


fig.update_layout(
    title="Contributions to the transition rate for the Ground state with Neumann b.c. on the static BTZ black hole",
    xaxis_title=r"$T_H$",
    yaxis_title=r"$\dot{\mathcal{F}}$"
)

fig.show()

## <span style='color:brown'>Sum in $l$</span>

### <span style='color:gray'>Precision settings exploration</span>

mp.dps = 500 is enough for the following plots.

In [91]:
mp.dps = 500

normalization_factor = 2.75

x = np.linspace(0, 30, 31)

def func0(l):
    return float(btz3.transition_rate_0(0, l,1/10, btz3.z_of_TH(100))[0])   
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

def func1(l):
    return float(btz3.transition_rate_0(0, l, 1/10, btz3.z_of_TH(100))[1])   
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))



fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0, name='Re'))
fig.add_trace(go.Scatter(x=x, y=y1, name='Im'))

fig.update_layout(
    title="The l terms for T=100",
    xaxis_title=r"$l$",
    yaxis_title=r"$\dot{\mathcal{F}}$"
)

fig.show()

<IPython.core.display.Javascript object>

In [92]:
mp.dps = 500

normalization_factor = 2.75

x = np.linspace(0, 30, 31)

def func0(l):
    return float(btz3.transition_rate_0(0, l, 1/10, btz3.z_of_TH(1))[0])   
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

def func1(l):
    return float(btz3.transition_rate_0(0, l, 1/10, btz3.z_of_TH(5))[0])   
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

def func2(l):
    return float(btz3.transition_rate_0(0, l, 1/10, btz3.z_of_TH(10))[0])   
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

def func3(l):
    return float(btz3.transition_rate_0(0, l, 1/10, btz3.z_of_TH(50))[0])   
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

def func4(l):
    return float(btz3.transition_rate_0(0, l, 1/10, btz3.z_of_TH(100))[0])   
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))


fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0, name='$T_H=1$'))
fig.add_trace(go.Scatter(x=x, y=y1, name='$T_H=5$'))
fig.add_trace(go.Scatter(x=x, y=y2, name='$T_H=10$'))
fig.add_trace(go.Scatter(x=x, y=y3, name='$T_H=50$'))
fig.add_trace(go.Scatter(x=x, y=y4, name='$T_H=100$'))


fig.update_layout(
    title="l terms of the transition rate for the Ground state on the static BTZ black hole",
    xaxis_title=r"$l_{max}$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Hawking temperatures"
)
fig.show()

<IPython.core.display.Javascript object>

### <span style='color:gray'>Summing up to $l_{max}$ 

####  <span style='color:olivedrab'> Ground state with Dirichlet boundary condition:</span>

In [93]:
mp.dps = 500
x = np.linspace(0, 30, 31)
normalization_factor = 2.75

def func0(l):
    return float(btz3.transition_rate_0(0, l, 1/10, btz3.z_of_TH(1))[0])/normalization_factor   
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

def func1(l):
    return float(btz3.transition_rate_0(0, l, 1/10, btz3.z_of_TH(5))[0])/normalization_factor  
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

def func2(l):
    return float(btz3.transition_rate_0(0, l, 1/10, btz3.z_of_TH(10))[0])/normalization_factor
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

def func3(l):
    return float(btz3.transition_rate_0(0, l, 1/10, btz3.z_of_TH(50))[0])/normalization_factor
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

def func4(l):
    return float(btz3.transition_rate_0(0, l, 1/10, btz3.z_of_TH(100))[0])/normalization_factor
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))


sumy0 = [y0[0]]
sumy1 = [y1[0]]
sumy2 = [y2[0]]
sumy3 = [y3[0]]
sumy4 = [y4[0]]
j = 0
while j < len(y1)-1:
    sumy0.append(sumy0[j] + y0[j + 1])
    sumy1.append(sumy1[j] + y1[j + 1])
    sumy2.append(sumy2[j] + y2[j + 1])
    sumy3.append(sumy3[j] + y3[j + 1])
    sumy4.append(sumy4[j] + y4[j + 1])
    j = j + 1 


fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=sumy0, name='$T_H=1$'))
fig.add_trace(go.Scatter(x=x, y=sumy1, name='$T_H=5$'))
fig.add_trace(go.Scatter(x=x, y=sumy2, name='$T_H=10$'))
fig.add_trace(go.Scatter(x=x, y=sumy3, name='$T_H=50$'))
fig.add_trace(go.Scatter(x=x, y=sumy4, name='$T_H=100$'))


fig.update_layout(
    title="Transition rate for the Ground state summed up to l_max on the static BTZ black hole",
    xaxis_title=r"$l_{max}$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Hawking temperatures"
)

fig.show()

####  <span style='color:olivedrab'> Ground state with Neumann boundary condition:</span>

In [94]:
mp.dps = 500
x = np.linspace(0, 30, 31)
normalization_factor = 2.75

def func0(l):
    return float(btz3.transition_rate_0(pi/2, l, 1/10, btz3.z_of_TH(1))[0])/normalization_factor   
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

def func1(l):
    return float(btz3.transition_rate_0(pi/2, l, 1/10, btz3.z_of_TH(5))[0])/normalization_factor   
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

def func2(l):
    return float(btz3.transition_rate_0(pi/2, l, 1/10, btz3.z_of_TH(10))[0])/normalization_factor   
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

def func3(l):
    return float(btz3.transition_rate_0(pi/2, l, 1/10, btz3.z_of_TH(50))[0])/normalization_factor   
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

def func4(l):
    return float(btz3.transition_rate_0(pi/2, l, 1/10, btz3.z_of_TH(100))[0])/normalization_factor   
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))


sumy0 = [y0[0]]
sumy1 = [y1[0]]
sumy2 = [y2[0]]
sumy3 = [y3[0]]
sumy4 = [y4[0]]
j = 0
while j < len(y0)-1:
    sumy0.append(sumy0[j] + y0[j + 1])
    sumy1.append(sumy1[j] + y1[j + 1])
    sumy2.append(sumy2[j] + y2[j + 1])
    sumy3.append(sumy3[j] + y3[j + 1])
    sumy4.append(sumy4[j] + y4[j + 1])
    j = j + 1 


fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=sumy0, name='$T_H=1$'))
fig.add_trace(go.Scatter(x=x, y=sumy1, name='$T_H=5$'))
fig.add_trace(go.Scatter(x=x, y=sumy2, name='$T_H=10$'))
fig.add_trace(go.Scatter(x=x, y=sumy3, name='$T_H=50$'))
fig.add_trace(go.Scatter(x=x, y=sumy4, name='$T_H=100$'))


fig.update_layout(
    title="Transition rate for the Ground state summed up to l_max on the static BTZ black hole",
    xaxis_title=r"$l_{max}$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Hawking temperatures"
)

fig.show()

####   <span style='color:olivedrab'> KMS state with Dirichlet boundary condition</span>

In [97]:
mp.dps = 500
x = np.linspace(0, 30, 31)
normalization_factor = 423500

def func0(l):
    return float(btz3.transition_rate_T(0, l, 1/10, btz3.z_of_TH(1))[0])/normalization_factor   
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

def func1(l):
    return float(btz3.transition_rate_T(0, l, 1/10, btz3.z_of_TH(5))[0])/normalization_factor   
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

def func2(l):
    return float(btz3.transition_rate_T(0, l, 1/10, btz3.z_of_TH(10))[0])/normalization_factor   
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

def func3(l):
    return float(btz3.transition_rate_T(0, l, 1/10, btz3.z_of_TH(50))[0])/normalization_factor   
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

def func4(l):
    return float(btz3.transition_rate_T(0, l, 1/10, btz3.z_of_TH(100))[0])/normalization_factor   
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))


sumy0 = [y0[0]]
sumy1 = [y1[0]]
sumy2 = [y2[0]]
sumy3 = [y3[0]]
sumy4 = [y4[0]]
j = 0
while j < len(y0)-1:
    sumy0.append(sumy0[j] + y0[j + 1])
    sumy1.append(sumy1[j] + y1[j + 1])
    sumy2.append(sumy2[j] + y2[j + 1])
    sumy3.append(sumy3[j] + y3[j + 1])
    sumy4.append(sumy4[j] + y4[j + 1])
    j = j + 1 


fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=sumy4, name='$T_H=100$'))
fig.add_trace(go.Scatter(x=x, y=sumy3, name='$T_H=50$'))
fig.add_trace(go.Scatter(x=x, y=sumy2, name='$T_H=10$'))
fig.add_trace(go.Scatter(x=x, y=sumy1, name='$T_H=5$'))
fig.add_trace(go.Scatter(x=x, y=sumy0, name='$T_H=1$'))


fig.update_layout(
    title="Transition rate for the KMS state summed up to l_max on the static BTZ black hole",
    xaxis_title=r"$l_{max}$",
    yaxis_title=r"$\dot{\mathcal{F}}$",
    legend_title="Hawking temperatures"
)

fig.show()

### <span style='color:gray'>It does look exponentially decreasing</span>

In [96]:
mp.dps = 500
normalization_factor = 2.75
x = np.linspace(0, 30, 31)

def func0(l):
    return float(log(btz3.transition_rate_0(0, l, 1/10, btz3.z_of_TH(1))[0]))/normalization_factor
vfunc0 = np.vectorize(func0)
y0 = (vfunc0((x)))

def func1(l):
    return float(log(btz3.transition_rate_0(0, l, 1/10, btz3.z_of_TH(5))[0]))/normalization_factor   
vfunc1 = np.vectorize(func1)
y1 = (vfunc1((x)))

def func2(l):
    return float(log(btz3.transition_rate_0(0, l, 1/10, btz3.z_of_TH(10))[0]))/normalization_factor   
vfunc2 = np.vectorize(func2)
y2 = (vfunc2((x)))

def func3(l):
    return float(log(btz3.transition_rate_0(0, l, 1/10, btz3.z_of_TH(50))[0]))/normalization_factor   
vfunc3 = np.vectorize(func3)
y3 = (vfunc3((x)))

def func4(l):
    return float(log(btz3.transition_rate_0(0, l, 1/10, btz3.z_of_TH(100))[0]))/normalization_factor  
vfunc4 = np.vectorize(func4)
y4 = (vfunc4((x)))


fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y0, name='$T_H=1$'))
fig.add_trace(go.Scatter(x=x, y=y1, name='$T_H=5$'))
fig.add_trace(go.Scatter(x=x, y=y2, name='$T_H=10$'))
fig.add_trace(go.Scatter(x=x, y=y3, name='$T_H=50$'))
fig.add_trace(go.Scatter(x=x, y=y4, name='$T_H=100$'))


fig.update_layout(
    title="log of l terms of the transition rate for the Ground state on the static BTZ black hole",
    xaxis_title=r"$l_{max}$",
    yaxis_title=r"$\log\dot{\mathcal{F}}$",
    legend_title="Hawking temperatures"
)
fig.show()

<IPython.core.display.Javascript object>

#  <span style='color:darkgreen'>As a function of the black hole mass</span>

To illustrate that the smaller the mass of the black hole, the more dominant the $l=0$ term becomes and the more irrelevant the higher $l$ contributions get, let's plot the $l=0$ and the $l=1$ as a function of $M$ for the set:
$$(\gamma,E_{gap}, z_D)=(0, 0.1,0.5). $$

In [123]:
mp.dps = 500

gamma0, lp, Egapp, zp = 0, 0,  0.1, 0.5

Ms      = np.array([0.01, 0.09, 0.16, 0.25, 0.36, 0.81, 1, 2.25, 4])
r_pluss = np.array([0.1,  0.3,  0.4,  0.5,  0.6,  0.9 , 1, 1.5, 2])
transitions = [float(BTZ(Ms[i], r_pluss[i]).transition_rate_0(gamma0, lp, Egapp, zp)[0]) for i in range(len(Ms))]

fig = go.Figure()
fig.add_trace(go.Scatter(x=Ms, y=transitions, name='Dirichlet'))


fig.update_layout(
    title="The l=0 contribution for different black hole masses",
    xaxis_title=r"$M$",
    yaxis_title=r"$\dot{\mathcal{F}}_{l=0}$"
)

fig.show()

In [108]:
mp.dps = 500

gamma0, lp, Egapp, zp = 0, 1,  0.1, 0.5

Ms      = np.array([0.01, 0.04, 0.09, 0.16, 0.25, 0.36, 0.49, 0.64, 0.81, 1, 2.25, 3.24, 4])
r_pluss = np.array([0.1,  0.2,  0.3,  0.4,  0.5,  0.6,  0.7,  0.8,  0.9 , 1, 1.5 , 1.8,  2])
transitions = [float(BTZ(Ms[i], r_pluss[i]).transition_rate_0(gamma0, lp, Egapp, zp)[0]) for i in range(len(Ms))]

fig = go.Figure()
fig.add_trace(go.Scatter(x=Ms, y=transitions, name='Dirichlet'))


fig.update_layout(
    title="The l=1 contribution for different black hole masses",
    xaxis_title=r"$M$",
    yaxis_title=r"$\dot{\mathcal{F}}_{l=1}$"
)

fig.show()

In [109]:
mp.dps = 500

gamma0, lp, Egapp, zp = 0, 2,  0.1, 0.5

Ms      = np.array([0.01, 0.04, 0.09, 0.16, 0.25, 0.36, 0.49, 0.64, 0.81, 1, 1.4, 2.25, 3.24, 4])
r_pluss = np.array([0.1,  0.2,  0.3,  0.4,  0.5,  0.6,  0.7,  0.8,  0.9 , 1, 1.2, 1.5 , 1.8,  2])
transitions = [float(BTZ(Ms[i], r_pluss[i]).transition_rate_0(gamma0, lp, Egapp, zp)[0]) for i in range(len(Ms))]

fig = go.Figure()
fig.add_trace(go.Scatter(x=Ms, y=transitions, name='Dirichlet'))


fig.update_layout(
    title="The l=2 contribution for different black hole masses",
    xaxis_title=r"$M$",
    yaxis_title=r"$\dot{\mathcal{F}}_{l=2}$"
)

fig.show()

In [113]:
mp.dps = 500

gamma0, lp, Egapp, zp = 0, 0,  0.1, 0.5

Ms      = np.array([0.01, 0.04, 0.09, 0.16, 0.25, 0.36, 0.49, 0.64, 0.81, 1, 2.25, 3.24, 4])
r_pluss = np.array([0.1,  0.2,  0.3,  0.4,  0.5,  0.6,  0.7,  0.8,  0.9 , 1, 1.5 , 1.8,  2])
transitions = [float(BTZ(Ms[i], r_pluss[i]).transition_rate_0(gamma0, 1, Egapp, zp)[0]/\
                     BTZ(Ms[i], r_pluss[i]).transition_rate_0(gamma0, 0, Egapp, zp)[0]) for i in range(len(Ms))]

fig = go.Figure()
fig.add_trace(go.Scatter(x=Ms, y=transitions, name='Dirichlet'))

fig.add_annotation(
        x=0.01,
        y=0.01,
        xref="x",
        yref="y",
        text=r"$(10^{-2},10^{-7})$",
        showarrow=True,
        font=dict(
            family="Courier New, monospace",
            size=14,
            color="#ffffff"
            ),
        align="center",
        arrowhead=2,
        arrowsize=1,
        arrowwidth=2,
        arrowcolor="#636363",
        ax=1,
        ay=-220,
        bordercolor="#c7c7c7",
        borderwidth=2,
        borderpad=6,
        bgcolor="#bb0eff",
        opacity=0.7
        )
fig.add_annotation(
        x=1,
        y=0.41,
        xref="x",
        yref="y",
        text=r"$(1,1)$",
        showarrow=True,
        font=dict(
            family="Courier New, monospace",
            size=14,
            color="#ffffff"
            ),
        align="center",
        arrowhead=2,
        arrowsize=1,
        arrowwidth=2,
        arrowcolor="#636363",
        ax=1,
        ay=-65,
        bordercolor="#c7c7c7",
        borderwidth=2,
        borderpad=6,
        bgcolor="#bb0eff",
        opacity=0.7
        )

fig.update_layout(
    title="The l=1 contribution divided by the l=0 one for different black hole masses",
    xaxis_title=r"$M$",
    yaxis_title=r"$\dot{\mathcal{F}}_{l=1}/\dot{\mathcal{F}}_{l=0}$",
    showlegend=False
)

fig.show()

The normalization as a function of the black hole mass:

In [124]:
mp.dps = 500

gamma0, lp, Egapp, zp = 0, 0,  0.1, 0.5

Ms      = np.array([0.01, 0.04, 0.09, 0.16, 0.25, 0.36, 0.49, 0.64, 0.81, 1, 2.25, 3.24, 4])
r_pluss = np.array([0.1,  0.2,  0.3,  0.4,  0.5,  0.6,  0.7,  0.8,  0.9 , 1, 1.5 , 1.8,  2])
transitions = [float(BTZ(Ms[i], r_pluss[i]).normalization(gamma0, lp, Egapp).real) for i in range(len(Ms)-1)]

fig = go.Figure()
fig.add_trace(go.Scatter(x=Ms, y=transitions, name='Dirichlet'))


fig.update_layout(
    title="The normalization for different black hole masses",
    xaxis_title=r"$M$",
    yaxis_title=r"$\mathcal{N}$"
)

fig.show()

#  <span style='color:darkgreen'>Conclusions</span>

From the plots above we can see that:

1. The behavior of the $l=0$ term of the transition rate for both the ground and the KMS states is the same w.r.t $(\gamma, z_D, T_H)$ for all values of $M$ up to a normalization constant;
2. The $l=0$ term for the ground state manifest "anti-Hawking effect"; for the KMS state, it does not.
3. Summing up more $l$ terms does switch the concavity of the curve for the KMS state, but it still doesn't manifest the effect.
4. The $l\geq0$ terms are smaller for smaller $M$, that is: the $l$-sum converges faster for smaller $M$. It indicates that:
    1. for $M=1$, the $l$-sum can cancell the "anti-Hawking effetct" for Dirichlet boundary condition, but not for Neumann
    2. $M=0.01$ is small enough to make the sum converge fast enough for the "anti-Hawking effect" for the effect to also be manifest for Dirichlet boundary condition. 